In [1]:
## Mini Dashboard map
import dash_daq as daq
import plotly
import plotly.express as px
import plotly.graph_objects as go
# import dash  # (version 1.12.0) pip install dash
#import dash_core_components as dcc
#import dash_html_components as html
from dash.dependencies import Input, Output

import numpy as np
from jupyter_dash import JupyterDash
import dash_bootstrap_components as dbc

import pandas as pd
from dash import html
from dash import dcc

# app = dash.Dash(__name__ , external_stylesheets= [dbc.themes.CYBORG])
# app = JupyterDash(__name__, external_stylesheets= [dbc.themes.CYBORG])
app = JupyterDash(__name__, )

# importing the modules for data reading and analysis (STATION DATA)

import sys
sys.path.append('modules')
from sensor_functions import *
from plot_functions_sensor import *

# Load and cleant the dataframe
df_res = pd.read_csv('sch_wmo_switch.csv', sep = '\t')
df_res = df_res.loc [ (df_res['delta_days'] != 'NA') &
                     (df_res['delta_days'] > 0) &
                     (df_res['sch'] != '-922') &
                     (df_res['wmo'] != 'NA ') &
                     (df_res['sch'] != 'NA ') &
                     (df_res['sch'] != df_res['wmo'] ) ]

df_res = df_res.reset_index()

# fill random vectors
# Must set compatible flag

df_res['compatible'] = 0
df_ress = df_res.sort_values(by=['station', 'delta_days'])


comp_df = pd.read_csv('compatible_wmo_sch.csv', sep='\t')

# to be displayed in separated TAB
sensor_table = comp_df[['sch', 'sch_comment', 'wmo', 'wmo_comment']]

comp = []
for i in range(len(df_res)):
    s = df_res['sch'][i].replace(' ', '')
    w = df_res['wmo'][i].replace(' ', '')

    sc = comp_df.loc[ comp_df.sch == s ]
    if len(sc) >0:
        comp.append(1)
    else:
        comp.append(0)

df_res['compatible'] = comp

"""
import random
for i in [1,2,3]:
    ind = list(random.sample( list(range(len(df_res)) ) , int(len(df_res)/3)  ) )
    df_res.loc[ind, 'compatible'] = i
"""

#text_cumsum = 'Cumulative Distribution of the last sensor metadta found in Schoreder, and the first entry found in WMO.\n '
#text_cumsum = text_cumsum + 'Around 50% of stations have metadata within '

default_station = "0-20000-0-06610" # "0-20000-0-82930" is fast, "0-20000-0-06610"



app.layout = html.Div([
    # title of our web page
    html.H1("Sensors Ids - Map Dashboard"),
    html.Br(),  # Br is a break i.e. a space in between

    dcc.Tabs([
        dcc.Tab( label='Map' ,
             children=[
                    html.Div([
                        html.Div(children=[
                            daq.ToggleSwitch( id='toggle', value=False, size=100,
                                #vertical=True,
                                label = { 'label': 'Schroeder / WMO', 'style': {'font-size': 20} },
                                style={'width': '10%', 'marginLeft': 50,'marginBottom': 40, 'marginTop': 40,
                                       'display': 'inline-block'},
                                ),
                            dcc.RadioItems(
                                id = 'radio',
                                options={ 'Compatible': 'Compatible', 'Incompatible': 'Incompatible'}, value = 'Compatible',
                                style = {'width': '49%', 'display': 'inline-block', 'marginLeft': 50,
                                      'padding-left': 40,  },
                                labelStyle={'display': 'block','text-align': 'justify', 'font-size': 25, },
                                ),

                            html.Br(), html.Br(),

                            html.Div([
                                    dcc.Graph(id='sensor_map', figure={},
                                              style={'display': 'inline-block', 'width': "50%",
                                                     }
                                              ),
                                    html.Div([
                                                html.Div([
                                                    dcc.Graph(id='bar1', figure={},
                                                             style={ 'width': "50%", 'display': 'inline-block',
                                                                     }
                                                              ),
                                                    dcc.Graph(id='bar2', figure={},
                                                             style={ 'width': "50%", 'display': 'inline-block'}
                                                              )
                                                    ], style={'display': 'inline-block', 'width': "100%" }) ,

                                                html.Div([
                                                    dcc.Graph(id='cumsum', figure={},
                                                             style={ 'display': 'inline-block' , 'width': "50%" } ),
                                                    ],

                                                    style={'display': 'inline-block', 'width': "100%"} ),

                            ],
                                            style={'display': 'inline-block', 'width': "50%"}
                                            )

                            ]),

                          ]
                        ),
                    ])
                 ]),

        dcc.Tab( label='Dataset Info',
                 children=[
                     html.Div([
                         dcc.Graph(id='table', figure={},
                                   style={'display': 'inline-block',
                                          'width': "100%",
                                          'marginLeft': '-10px'}),
                     ],
                         style={'width': '100%',
                                'display': 'inline-block',
                                },
                         className="dash-container", )
                 ],
        ),

        dcc.Tab(label='Sensor',
                children=[
                    html.Div([
                        dcc.Graph(id='table_sensor', figure={},
                                  style={'display': 'inline-block', 'width': "100%", 'marginLeft': '-10px'}),
                        ],
                        style={'width': '100%', 'display': 'inline-block', },
                        )
                ],
                ),


        dcc.Tab(label='Station Data',
                children=[
                    html.H1("Sensor Id Metadata Dashboard",
                            style={'text-align': 'center'}),

                    html.Br(),  # Br is a break i.e. a space in between

                    html.Div([

                        html.Div(children=[
                            html.Label('Station Primary Id'),
                            dcc.Input(id="input_station",
                                      type="text",
                                      placeholder=default_station,
                                      style={'marginLeft': '20px' , 'size':50},
                                      value=default_station,
                                      debounce=True,  # to wait for click on Enter to start data retrieval
                                      ),
                            dcc.Loading(id="loading-1",
                                        type="circle",
                                        children=html.Div(id="loading-output-1")
                                        ),
                        ]),

                        html.Div(children=[
                            dcc.Graph(id='series', figure={},
                                      # how to make two dcc close by: use inline-block and inside same html.Div as children
                                      style={'display': 'inline-block',
                                             'width': "71%",
                                             'marginRight': '-10px',
                                             'marginLeft': '-10px'}),

                            dcc.Graph(id='wmo_table', figure={},
                                      style={'display': 'inline-block',
                                             'width': "28%",
                                             'marginLeft': '-10px'}),
                        ],
                            style={'width': '100%',
                                   'display': 'inline-block',
                                   },
                            className="dash-container", ),

                        html.Div([
                            html.H1("Sensor Description"),

                            dcc.Graph(id='sensor_table_red', figure={},
                                      style={'display': 'inline-block',
                                             'width': "100%",
                                             'marginLeft': '-10px'} ),

                            html.H1("Complete Sensor Data with Time Stamps"),

                            dcc.Graph(id='sensor_table_all', figure={},
                                      style={'display': 'inline-block',
                                             'width': "100%",
                                             'marginLeft': '-10px'}),

                        ],
                            style={'width': '100%',
                                   'display': 'inline-block',
                                   },


                         ),

                    ])


                ],
                ),

    ]),

])

@app.callback(
    [Output(component_id='sensor_map', component_property='figure'),
     Output(component_id='bar1',  component_property='figure' ),
     Output(component_id='bar2',  component_property='figure' ),
     Output(component_id='cumsum', component_property='figure'),

     ],

    [Input('toggle', 'value'),
     Input('radio', 'value')]
)

def plots(toggle, radio):
    # mapping the compatible, incompatible, all stations
    comp_dic = {'All' : 2,
           "Compatible": 1,
           "Incompatible": 0 }

    df_res_ = df_res.loc[df_res['compatible'] == comp_dic[radio] ]

    df_res_.wmo = df_res_.wmo.astype(int).astype(str)
    # to select a color bar: https://plotly.com/python/discrete-color/

    if not toggle:
        id = "SCHROEDER"
        title = id + ' Sensor Ids'
        col = df_res_.sch
        cb = px.colors.qualitative.G10
    else:
        id = "WMO"
        title = id + ' Sensor Ids'
        col = df_res_.wmo
        cb = px.colors.qualitative.Plotly

    # Creating maps
    title = title + '  for ' + radio + '  Sensors'
    map = px.scatter_geo(df_res_,
                         lat=df_res_.latitude,
                         lon=df_res_.longitude,
                         hover_name="station",
                         hover_data={"sch" : True,
                                     "wmo" : True,
                                     'latitude': False,
                                     'longitude': False,
                                     'station_name': True,
                                     'compatible':True,
                                     'delta_days':True},
                         color=col,
                         color_discrete_sequence= cb,
                         )

    # see bottom https://community.plotly.com/t/margins-around-graphs/11550/4
    map.update_layout(
        height=900, width=1200,
        title= { 'text': title,  "yref": "paper","y": 1, "yanchor": "bottom" },
        #xaxis_title="X Axis Title",
        #yaxis_title="Y Axis Title",
        font=dict( family="Courier New, monospace", size=20, #color="RebeccaPurple"
        ),
        # margin=dict(l=20, r=20, t=0, b=5),
        legend=dict(font=dict(family="Courier New, monospace", size=25, color="black"), title = "Sensor Id"),
        legend_title=dict(font=dict(family="Courier New, monospace", size=25, color="blue"))
    )

    # Creating bar plots
    df_res_['wmo'] = df_res_.wmo.astype(str)

    bar_sch = px.histogram(df_res_, x="sch").update_xaxes(categoryorder='total descending')
    bar_sch.update_layout(
        height=500, width=500,
        title= { 'text': "Schroeder Id Counts",  "yref": "paper", "yanchor": "bottom" },
        font=dict( family="Courier New, monospace", size=20, #color="RebeccaPurple"
        ),
    xaxis_title="" )

    bar_wmo = px.histogram(df_res_, x="wmo").update_xaxes(categoryorder='total descending')
    bar_wmo.update_layout(
        height=500, width=500,
        title= { 'text': "WMO Id Counts",  "yref": "paper", "yanchor": "bottom" },
        font=dict( family="Courier New, monospace", size=20, #color="RebeccaPurple"
        ),
    xaxis_title="" )

    #creating cumsum plot
    cumvalues = np.log(df_res_['delta_days'])
    cumsum = go.Figure(data=[go.Histogram(x=cumvalues,  nbinsx=20,
                                          cumulative_enabled=True, histnorm='probability density' )],)

    #cumsum.update_xaxes(type="log")  # log range: 10^0=1, 10^5=100000
    cumsum.update_layout( title = {'text': "Cumulative Sum of Stations", "yref": "paper", "yanchor": "bottom"},
                          font=dict(family="Courier New, monospace", size=20,  # color="RebeccaPurple"
                                    ),
                          xaxis_title="Log10(Delta Days)",
                          )

    return [map, bar_sch, bar_wmo, cumsum]


@app.callback(
    [
     Output(component_id='table', component_property='figure' ),
     Input('toggle', 'value')
     ],

)

def make_table(toggle):

    #df_ress = df_res.sort_values(by=['station','delta_days'])

    # replacing labels for table
    comp = [ 'True' if  v==1 else 'False' for v in df_ress.compatible.values ]
    df_ress['compatible'] = comp

    # Plotting the table

    table = go.Figure(data=[go.Table(
        header=dict(values=list(
            ['Station', 'Schroeder', 'Schroeder Date', 'WMO', 'WMO Date', 'Delta Days', 'Data Start', 'Data End',
             'Total Records', 'Compatible']),
                    fill_color='turquoise',
                    align='left',
                    font_size=16),
        columnwidth=[5, 3, 4, 3, 4, 3, 4, 4, 3, 3],

        cells=dict(values=[df_ress.station, df_ress.sch, df_ress.sch_date,
                           df_ress.wmo, df_ress.wmo_date,
                           df_ress.delta_days,
                           df_ress.min_date,
                           df_ress.max_date,
                           df_ress.records,
                           df_ress.compatible,
                           ],

                   fill_color='aliceblue',
                   align='left',
                   font_size=15,
                   line_color='darkslategray',
                   fill=dict(color=['paleturquoise', 'white']),
                   height=25)
    )])

    table.update_layout(height=1500, width=1500)
    return[table]

@app.callback(
    [
     Output(component_id='table_sensor', component_property='figure' ),
     Input('toggle', 'value')
     ],

)


def make_table_sensor(toggle):
    #sensor_table #['sch', 'sch_comment', 'wmo', 'wmo_comment']

    table = go.Figure(data=[go.Table(
        header=dict(values=list(
            ['Schroeder ID', 'Schroeder Description', 'WMO ID', 'WMO Description']),
                    fill_color='orange',
                    align='left',
                    font_size=16),
        columnwidth=[3, 10, 3, 10],

        cells=dict(values=[sensor_table.sch,
                           sensor_table.sch_comment,
                           sensor_table.wmo,
                           sensor_table.wmo_comment
                           ],

                   fill_color='yellow',
                   align='left',
                   font_size=15,
                   line_color='black',
                   fill=dict(color=['paleturquoise', 'white']),
                   height=25)

    )])

    table.update_layout(height=1000, width=2000)

    return[table]


@app.callback(
    [Output(component_id='series', component_property='figure'),
     Output(component_id='wmo_table', component_property='figure'),
     Output(component_id='sensor_table_red', component_property='figure'),
     Output(component_id='sensor_table_all', component_property='figure'),

     ],

    [Input(component_id='input_station', component_property='value')
     ]

)

def update_plots(station):
    """ Function to call back """

    # Extracting all the data
    # all_data , all_sensor = get_data(station)

    if station not in ['0-20001-0-10393' ,'0-20000-0-06610' , '0-20001-0-11035' ]:
        station = '0-20001-0-10393'

    data_clean_all, all_sensor_station, data_all_wmo = get_data('', station, force_create=False)

    # Loading the chart class """
    plot = Plot(station.split('_')[-1], save=False)


    # Creating the plots
    sensor_table_red = plot.sensor_table_red(all_sensor_station)
    series = plot.time_series(data_clean_all, label='')
    wmo_table = plot.wmo_bar_plot(data_all_wmo)
    sensor_table_a = plot.sensor_table_alldata(data_clean_all)


    # Defined here, not taken from external module
    # data clean all ['date_time', 'sensor_id', 'value', 'source', 'comment', 'moment']
    fs = 30

    sensor_table_all = go.Figure(data=[go.Table(
        header=dict(values=list(['Timestamp', 'Sensor', 'Source' , 'Description', 'Day time']),
                    fill_color='gold',
                    align='left',
                    font_size=fs),
        columnwidth=[4, 2, 2,8,3],

        cells=dict(values=[data_clean_all.date_time,
                           data_clean_all.sensor_id,
                           data_clean_all.source,
                           data_clean_all.comment,
                           data_clean_all.moment],

                   fill_color='aliceblue',
                   align='left',
                   font_size=fs,
                   line_color='darkslategray',
                   fill=dict(color=['paleturquoise', 'white']),
                   height=25
                   )

    )])


    return [series, wmo_table, sensor_table_red, sensor_table_a ]

In [2]:
if __name__ == '__main__':
    #app.run_server(mode = 'inline', debug=True)
    import socket
    host = socket.gethostbyname(socket.gethostname())
    app.run_server(port=8048, debug=True, host = host)
    #app.run_server(debug=True, host = host)
    # app.run_server(host='0.0.0.0', debug=True)

Dash app running on http://131.130.157.8:8048/
cond is  True
cond combi is  False
cond is  True
cond combi is  False
cond is  True
cond combi is  False
cond is  True
cond combi is  False
